In [126]:
import math
import pickle
import requests 
import json
import string
from pprint import pprint
from collections import Counter, defaultdict

from nltk import sent_tokenize, word_tokenize, pos_tag, ne_chunk
from nltk.corpus import stopwords
#from nameparser.parser import HumanName

In [2]:
with open("guardian_api.txt", 'r') as f:
    api_key = f.next().strip()

In [3]:
def get_content(pg):
    api_url = 'http://content.guardianapis.com/search'
    payload = {
        'api-key':              api_key,
        'page-size':            50,
        'page':                 pg,
        'q':                    'party OR policy OR democrat OR republican', 
        #'order-by':             'newest',
        #'show-editors-picks':   'true',
        #'show-elements':        'image',
        'show-blocks':          'body',
        'show-fields':          'byline, wordcount',
        #'show-tags':            'all',
        #'show-references':      'author',
        'format':               'json'
    }
    response = requests.get(api_url, params=payload)
    #response = response.replace("'", '"')
    #data = json.loads(response)
    data = response.json() # convert json to python-readable format 
    return data


In [4]:
all_data = []
for i in range(1, 6):
    data = get_content(i)
    print data["response"]["status"]
    res = data["response"]["results"]
    all_data += res
#print data["response"]["status"]

ok
ok
ok
ok
ok


In [5]:
print len(all_data)

250


In [6]:
#pprint(res[0])
pprint(all_data[0])

{u'apiUrl': u'http://content.guardianapis.com/us-news/2015/jun/09/carly-fiorina-foreign-policy-republican-interview',
 u'blocks': {u'body': [{u'attributes': {},
                        u'bodyHtml': u'<p>Carly Fiorina has chutzpah. The former CEO of Hewlett Packett isn\u2019t just running for the Republican nomination for president <a href="http://www.theguardian.com/us-news/2015/may/03/carly-fiorina-run-for-president-hewlett-packard">on a platform of managerial expertise</a> after a controversial tenure at that technology company from 1999 to 2005. She\u2019s running as a foreign policy maven despite having never served in elected office.</p> <p>In an interview with the Guardian on Saturday, Fiorina bragged that she \u201cknows more world leaders on the stage\u201d than any of her competitors for the 2016 nomination, a claim she echoed in a speech shortly afterwards at Iowa senator Joni Ernst\u2019s <a href="http://www.theguardian.com/us-news/2015/jun/06/republican-2016-iowa-joni-ernst

In [7]:
print(all_data[0]["blocks"]["body"][0]["bodyTextSummary"])
print(all_data[0]["fields"]["byline"])

Carly Fiorina has chutzpah. The former CEO of Hewlett Packett isn’t just running for the Republican nomination for president on a platform of managerial expertise after a controversial tenure at that technology company from 1999 to 2005. She’s running as a foreign policy maven despite having never served in elected office. In an interview with the Guardian on Saturday, Fiorina bragged that she “knows more world leaders on the stage” than any of her competitors for the 2016 nomination, a claim she echoed in a speech shortly afterwards at Iowa senator Joni Ernst’s inaugural Roast and Ride fundraiser. The former CEO argued that she “conducted business and charitable work” with world leaders “for many years”. She contrasted herself with mere politicians by saying: “I don’t do photo ops. I don’t do codels [congressional delegations].” Fiorina insisted “I know these people. I know how they think about us.” Her foreign policy worldview, though, seemed to be more focused on criticism of the Ob

In [8]:
'''def get_human_names(text):
    tokens = word_tokenize(text)
    pos = pos_tag(tokens)
    sentt = ne_chunk(pos)#, binary = False)
    person_list = []
    person = []
    name = ""
    print sentt
    for subtree in sentt.subtrees(filter=lambda t: t.label() == 'PERSON'):
        for leaf in subtree.leaves():
            person.append(leaf[0])
        if len(person) > 1: #avoid grabbing lone surnames
            for part in person:
                name += part + ' '
            #if name[:-1] not in person_list:
            person_list.append(name[:-1])
            name = ''
        person = []

    return (person_list)'''

def get_human_names(text):
    if " and " in text or " with " in text:
        #don't really deal with multiple authors
        return text
    elif " in " in text:
        #assume same name in different locations is 
        # still the same person
        ind = text.find(" in ")
        return text[:ind]
    else:
        return text

In [64]:
def dd():
    return ""

def make_dict(loc=False):
    authors = []
    names = []
    auth_ar = defaultdict(dd)
    for b in range(len(all_data)):
        if "fields" in all_data[b]:
            if "blocks" in all_data[b]:
                #print b
                nm = all_data[b]["fields"]["byline"].strip().decode("utf-8")
                #print nm
                authors.append(nm)
                if not loc:
                    nm = get_human_names(str(all_data[b]["fields"]["byline"]))
                names.append(nm)
                auth_ar[nm] += all_data[b]["blocks"]["body"][0]["bodyTextSummary"]
    return names, auth_ar
names, auth_ar = make_dict()
print names, "\n", len(names)
#pprint(authors)
counts = Counter(names)
print(counts)

['Ben Jacobs', 'Frances Perraudin', 'Ben Jacobs', 'Scott Keyes', 'Michael Cohen', 'Ben Jacobs', 'Paul Lewis', 'Ben Jacobs', 'Ben Jacobs in Washington, Sabrina Siddiqui  in Manchester and Jeb Lund', 'Ryan Felton', 'Alan Yuhas with Paul Lewis in Cleveland, Jeb Lund in Tampa, Ben Jacobs in Atlanta, Dan Roberts and Sabrina Siddiqui in Washington and Adam Gabbatt in New York', 'Amanda Holpuch', 'Tom McCarthy', 'Tom Dart', 'Martin Kettle', 'Jeb Lund', 'Sabrina Siddiqui', 'Paul Lewis', 'Observer editorial', 'Dan Roberts', 'Frances Perraudin', 'Paul Lewis', 'Dan Roberts and Sabrina Siddiqui Washington', 'David Boyle', 'Rupert Myers', 'Paul Lewis', 'Ben Jacobs', 'Paul Lewis', 'Anna Leach', 'Jeb Lund', 'Alan Yuhas', 'Scott Lemieux', 'Sabrina Siddiqui', 'Alan Yuhas', 'Paul Lewis', 'Alan Yuhas', 'Patrick Wintour, political editor', 'Frances Perraudin', 'Ben Jacobs in Washington and Alan Yuhas in New York', 'Gary Younge', 'Tom McCarthy', 'Paul Lewis ', 'Frances Perraudin', 'Sabrina Siddiqui', 'Tom 

In [65]:
print len(auth_ar["Frances Perraudin"])

23240


In [66]:
print len(sent_tokenize(auth_ar["Paul Lewis"]))

607


In [67]:
sents = {}
for author, text in auth_ar.iteritems():
    sent = sent_tokenize(text)
    if len(sent) > 100:
        sents[author] = sent
        print author, len(sent)

Frances Perraudin 108
Rowena Mason Political correspondent 114
Sabrina Siddiqui 550
Lauren Gambino 148
Daniel Boffey 121
Donna Ferguson 107
Paul Lewis 607
Tom McCarthy 515
Tom Dart 172
Dan Roberts 412
Alan Yuhas 261
Ben Jacobs 535
Jeb Lund 417


In [68]:
with open("author_articles.pkl", 'w') as out_auth_ar:
    pickle.dump(auth_ar, out_auth_ar)
with open("auth_sents.pkl", 'w') as outs:
    pickle.dump(sents, outs)

In [133]:
def get_frequencies(len_w, counts, subset=False):
    '''takes number tokens as float,list of (k, v), and converts v from int count to frequency.
    If subset, takes frequency over the counts rather than the whole
    set of tokens'''
    freqs = []
    sorted_counts = zip(*sorted(counts.items()))[1]
    if subset:
        countsum = float(sum(sorted_counts))
        freqs = [sc/countsum for sc in sorted_counts]
    else:
        for sc in sorted_counts:
            fs = sc/len_w
            if fs > 0.0:
                f = math.log(fs)
                freqs.append(f)
            else:
                freqs.append(0.0)
    return freqs

In [141]:
#sen_features = {}

sp = string.punctuation
sp = unicode(sp)
punct = [s for s in sp]
punct.append(u'``')
punct.append(u"''")
punct.append(u'\u2013')

#print punct, len(punct)
swords = stopwords.words('english')
swords.append('\'s')
swords.append('\'t')
#print swords

featuresli = []
authors = []
    
def pd():
    return 0

for author, sentences in sents.iteritems():
    print author
    
    for s in sentences:
        #punct_counts = defaultdict(pd)
        punct_counts = dict.fromkeys(punct, 0)
        sword_counts = dict.fromkeys(swords, 0)
        features = []
        len_w = 0.0
        count_w = 0.0
        s = s.replace(u"\u2018", "'").replace(u"\u2019", "'") \
            .replace(u"\u201c",'"').replace(u"\u201d", '"') \
            .replace(u"\u030F", '"').replace(u"''", '"')
        words = word_tokenize(s) #punctuation is included as words
        #print s, "\n", [s]
        #print len(words)
        for word in words:
            word = word.lower()
            #print word, [word]               
            if word in punct:# or word[0] in punct:
                punct_counts[word] += 1
            elif word in swords:
                sword_counts[word] += 1
            len_w += len(word)
            count_w += 1
        avg_wlen = len_w/count_w
        #print avg_wlen
        punct_freq = get_frequencies(len_w, punct_counts)#zip(*sorted(punct_counts.items()))[1]
        sword_freq = get_frequencies(len_w, sword_counts)#zip(*sorted(sword_counts.items()))[1]
        #print punct_freq
        #print sword_freq
        #print sorted(sword_counts.items())
        features.append(len(words)) #total number of tokens in sentence
        features.append(avg_wlen) #average word/token length
        features += punct_freq #frequency of punctuation tokens
        features += sword_freq #frequency of stopword tokens
        featuresli.append(features)
        authors.append(author)

print authors
print featuresli
        

Lauren Gambino
Daniel Boffey
Donna Ferguson
Jeb Lund
Alan Yuhas
Dan Roberts
Paul Lewis
Tom McCarthy
Frances Perraudin
Rowena Mason Political correspondent
Sabrina Siddiqui
Ben Jacobs
Tom Dart
['Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino', 'Lauren Gambino

In [142]:
with open("authors.pkl", 'w') as out_auths:
    pickle.dump(authors, out_auths)
with open("features.pkl", 'w') as outs:
    pickle.dump(featuresli, outs)